# Train datatset

Investigate the train dataset, similar but longer than test dataset.

Every row in this dataset represents the number of sales and promotion per day, store and product family

In [1]:
# import libs
import pandas as pd
import numpy as np
from pandas_profiling import ProfileReport

from definitions import TRAIN_FILE

# load data
train_df = pd.read_csv(TRAIN_FILE)
train_df['date'] = pd.to_datetime(train_df['date'])
train_df['store_nbr'] = train_df['store_nbr'].astype('category')
report = ProfileReport(train_df, title="Train dataset report.", infer_dtypes=False)

# remove outliers.
train_df['sales'] = train_df['sales'].clip(upper=2500)
train_df['onpromotion'] = train_df['onpromotion'].clip(upper=2500)

# uncomment to save as html file if you rather look at the report in your browser.
# report.to_file('train_data_report.html')
report.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

observations:
- sales and promotion have a lot of zero's. but no missing data.
- sales and promotion have outliers (already clipped in this report).
- there is a mild correlation between product family and promotions

## 0 sales or promotions.
lets replace the 0's in the sales and onpromotion columns with nan's and see if there is a pattern in the missing data matrix.
Also we group the data by stores and product families so that eacht column in the matrix is the full sales/onpromotion of one store through time.


In [2]:
data_by_store = []
for store_nbr, store_df in train_df[['date' ,'store_nbr', 'sales', 'onpromotion']].groupby('store_nbr'):
    store_df = store_df.groupby('date').sum()
    store_df = store_df[['sales', 'onpromotion']].rename(columns={'sales': 'sales_' + str(store_nbr), 'onpromotion': 'onpromotion_' + str(store_nbr)})
    data_by_store.append(store_df)

grouped_by_store = pd.concat(data_by_store, axis=1)

# consider 0 data as nan.
grouped_by_store[grouped_by_store < 1] = np.NAN
# grouped_by_store.replace(0, np.NAN)

# create minimal (descriptives only) profile report.
report = ProfileReport(grouped_by_store, title="Transactions dataset report.", minimal=True)
# manually enable matrix to visualise missing data.
report.config.missing_diagrams = {'bar': False, 'matrix': True, 'heatmap': False, 'dendrogram': False}

# uncomment to save as html file if you rather look at the report in your browser.
# report.to_file('train_data_report_clipped.html')
report.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

observations:
 - Sales data doesnt seem to have a lot of 0's.
 - Only 0's in sales data are when the store doesn't exist year or is closed for a longer time, the same pattern can bee seen in the transaction dataset.
 - almost no promotions before approximately mid 2014. After that every store has pretty much continuous promotions.

 ## promotion per family correlation.

In [3]:
family_table = train_df[['family', 'sales', 'onpromotion']].groupby('family').sum()
family_table['sales_k'] = family_table['sales'] / 1000
family_table['ratio'] = family_table['onpromotion'] / family_table['sales_k']
print(family_table[['sales_k', 'onpromotion', 'ratio']].sort_values('ratio', ascending=False))

                                  sales_k  onpromotion      ratio
family                                                           
SCHOOL AND OFFICE SUPPLIES     269.316000        14565  54.081451
BEAUTY                         337.893000        13483  39.903165
HOME AND KITCHEN I            1861.491000        46921  25.206139
DELI                         24110.322469       583316  24.193621
HOME AND KITCHEN II           1520.670000        32814  21.578646
LAWN AND GARDEN                548.842000        11208  20.421178
SEAFOOD                       2015.431883        39052  19.376492
PRODUCE                      79586.641665      1117921  14.046591
EGGS                         15586.075000       194922  12.506163
HOME CARE                    16022.740000       197230  12.309380
DAIRY                        62948.405000       728707  11.576258
PERSONAL CARE                24572.732000       246928  10.048862
GROCERY I                   193825.062950      1914801   9.879017
MEATS     

Observations:
 - There is a lot of variation in how often different product families are promoted per sale.

In [4]:
store_table = train_df[['store_nbr', 'sales', 'onpromotion']].groupby('store_nbr').sum()
store_table['sales_k'] = store_table['sales'] / 1000
store_table['ratio'] = store_table['onpromotion'] / store_table['sales_k']
print(store_table[['sales_k', 'onpromotion', 'ratio']].sort_values('ratio', ascending=False))

                sales_k  onpromotion      ratio
store_nbr                                      
22          3958.325982        99543  25.147752
53         10161.964168       204016  20.076434
21          7605.565382       144062  18.941656
29          8432.192722       153632  18.219697
52          1725.054020        30814  17.862629
20          9604.111051       157358  16.384442
42          7878.066122       124670  15.824950
32          5822.793981        89932  15.444819
26          7510.802107       111498  14.845019
35          7518.015368       110104  14.645354
30          7302.071030       103096  14.118734
54         10142.394092       142724  14.072023
36         13252.266766       158527  11.962255
12         10158.495846       117657  11.582128
10          9193.577152       103223  11.227730
23         11578.010594       128989  11.140860
15         10857.513373       120308  11.080622
16         10390.473203       114197  10.990549
18         12270.548609       134087  10

Observations:
 - There is a less variation in how often different stores have promotions in relation to their sales.


## promotion sales relation.

Lets see how strong the relation between promotions and sales is.
We use the data grouped by store and correlate the number of promotions with the number of sales.
As we do this we also shift the sales figures into the future to see if this improves the correlation.

In [11]:
# correlate onpromotion and sales per product family, try shifted.
# filter dates after august 2014 as no promotions where recorded before mid 2014.
promo_sales = grouped_by_store.loc[grouped_by_store.index > '2014-08-01']
# drop columns with a lot of missing data, these are stores that weren't open during the the full period.
na_thresh = len(promo_sales) * 0.9
promo_sales = promo_sales.dropna(thresh=na_thresh, axis=1)

for shift_n in range(0, 31):
    promo_sales_correlation_results = []
    #loop through stores.
    for column_name in promo_sales.columns:
        column_type, store_nbr = column_name.split('_')
        if column_type == 'onpromotion':
            # ignore columns with promotion data, only handle columns with sales data.
            continue

        # Shift sales figures n days into the future.
        shifted_sales = promo_sales[column_name].shift(shift_n)
        # cut promo figure to size of shifted sales figures.
        cut_promo = promo_sales[shift_n:]['onpromotion_' + store_nbr]
        # correlate current promo figures with future sales figures.
        promo_sales_correlation = shifted_sales.corr(cut_promo)
        # print(f'correlation for store {store_nbr: >3} is {promo_sales_correlation:>5.2f}') # uncomment to see every result.
        promo_sales_correlation_results.append(promo_sales_correlation)

    print(f'average_correlation: {sum(promo_sales_correlation_results)/len(promo_sales_correlation_results):.2f} (shifted {shift_n})')

average_correlation: 0.29 (shifted 0)
average_correlation: 0.16 (shifted 1)
average_correlation: 0.26 (shifted 2)
average_correlation: 0.34 (shifted 3)
average_correlation: 0.32 (shifted 4)
average_correlation: 0.33 (shifted 5)
average_correlation: 0.22 (shifted 6)
average_correlation: 0.26 (shifted 7)
average_correlation: 0.15 (shifted 8)
average_correlation: 0.25 (shifted 9)
average_correlation: 0.33 (shifted 10)
average_correlation: 0.32 (shifted 11)
average_correlation: 0.31 (shifted 12)
average_correlation: 0.21 (shifted 13)
average_correlation: 0.25 (shifted 14)
average_correlation: 0.14 (shifted 15)
average_correlation: 0.24 (shifted 16)
average_correlation: 0.32 (shifted 17)
average_correlation: 0.31 (shifted 18)
average_correlation: 0.30 (shifted 19)
average_correlation: 0.20 (shifted 20)
average_correlation: 0.23 (shifted 21)
average_correlation: 0.13 (shifted 22)
average_correlation: 0.23 (shifted 23)
average_correlation: 0.31 (shifted 24)
average_correlation: 0.30 (shifted 

conclusion is that there is no strong (direct) relation between the number of promotions and number of sales in a particular store.
Perhaps specific product families are promoted, we can apply the same logic to product families.

In [12]:

grouped_by_family = []
for family_name, family_df in train_df[['date', 'family', 'sales', 'onpromotion']].groupby('family'):
    family_df = family_df.groupby('date').sum()
    family_df = family_df[['sales', 'onpromotion']].rename(columns={'sales': 'sales_' + family_name,'onpromotion': 'onpromotion_' + family_name})
    grouped_by_family.append(family_df)

grouped_by_family = pd.concat(grouped_by_family, axis=1)
grouped_by_family[grouped_by_family < 1] = np.NAN

# correlate onpromotion and sales per product family, try shifted.
# filter dates after august 2014 as no promotions where recorded before mid 2014.
promo_sales = grouped_by_family.loc[grouped_by_family.index > '2014-08-01']
# drop columns with a lot of missing data, these are stores that weren't open during the full period.
promo_sales = promo_sales.fillna(0)

for shift_n in range(0, 31):
    promo_sales_correlation_results = []
    for column_name in promo_sales.columns:
        column_type, store_nbr = column_name.split('_')
        if column_type == 'onpromotion':
            continue

        # Shift sales figures n days into the future.
        shifted_sales = promo_sales[column_name].shift(shift_n)[shift_n:]
        # cut promo figure to size of shifted sales figures.
        cut_promo = promo_sales[shift_n:]['onpromotion_' + store_nbr]
        # correlate current promo figures with future sales figures.
        promo_sales_correlation = shifted_sales.corr(cut_promo)
        if np.isnan(promo_sales_correlation):
            continue
        # print(f'correlation for store {store_nbr: >3} is {promo_sales_correlation:>5.2f}') # uncomment to see every result.
        promo_sales_correlation_results.append(abs(promo_sales_correlation))

    print(f'average_correlation: {sum(promo_sales_correlation_results)/len(promo_sales_correlation_results):.2f} (shifted {shift_n})')

average_correlation: 0.27 (shifted 0)
average_correlation: 0.24 (shifted 1)
average_correlation: 0.19 (shifted 2)
average_correlation: 0.23 (shifted 3)
average_correlation: 0.20 (shifted 4)
average_correlation: 0.22 (shifted 5)
average_correlation: 0.21 (shifted 6)
average_correlation: 0.24 (shifted 7)
average_correlation: 0.22 (shifted 8)
average_correlation: 0.19 (shifted 9)
average_correlation: 0.22 (shifted 10)
average_correlation: 0.19 (shifted 11)
average_correlation: 0.21 (shifted 12)
average_correlation: 0.20 (shifted 13)
average_correlation: 0.23 (shifted 14)
average_correlation: 0.21 (shifted 15)
average_correlation: 0.17 (shifted 16)
average_correlation: 0.21 (shifted 17)
average_correlation: 0.18 (shifted 18)
average_correlation: 0.19 (shifted 19)
average_correlation: 0.18 (shifted 20)
average_correlation: 0.21 (shifted 21)
average_correlation: 0.20 (shifted 22)
average_correlation: 0.16 (shifted 23)
average_correlation: 0.20 (shifted 24)
average_correlation: 0.17 (shifted 

Just like with stores there is no (direct) relation between promotions ans sales when looking at products.